<link rel="stylesheet" href="../../styles/theme_style.css">
<link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/4.7.0/css/font-awesome.min.css">

<table width="100%">
    <tr>
        <td id="image_td" width="15%" class="header_image_color_4"><div id="image_img" class="header_image_4"></div></td>
        <td class="header_text"> Digital Filtering - Using filtfilt </td>
    </tr>
</table>

<div id="flex-container">
    <div id="diff_level" class="flex-item">
        <strong>Difficulty Level:</strong>   <span class="fa fa-star checked"></span>
                                <span class="fa fa-star"></span>
                                <span class="fa fa-star"></span>
                                <span class="fa fa-star"></span>
                                <span class="fa fa-star"></span>
    </div>
    <div id="tag" class="flex-item-tag">
        <span id="tag_list">
            <table id="tag_list_table">
                <tr>
                    <td class="shield_left">Tags</td>
                    <td class="shield_right" id="tags">pre-process&#9729;filter&#9729;filtfilt</td> 
                </tr>
            </table>
        </span>
        <!-- [OR] Visit https://img.shields.io in order to create a tag badge-->
    </div>
</div>

As it has been mentioned in a previous  <strong><span class="color5">Jupyter Notebook</span></strong> concerning  <a href="https://en.wikipedia.org/wiki/Noise_(signal_processing)" target="_blank">digital filtering <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a>, recorded signals usually contain noise, which may have different origins, that has to be minimized as much as possible to obtain a high quality signal with the highest achievable signal to noise ratio. 

This <strong><span class="color5">Jupyter Notebook</span></strong> will focus on the use of an specific type of digital filter: the <strong>filtfilt</strong>, also known as zero phase filtering or forward and backwards digital filter. It applies the same filter twice: once forwards and once backwards. This combination results in a filter with zero phase distortion and an order that is twice that of the original filter.

This type of filtering is really useful to preserve features in a filtered time waveform exactly where they occur in the unfiltered signal.

<p class="steps">1 - Importation of the needed packages</p>

In [1]:
# biosignalsnotebooks own package for loading and plotting the acquired data
import biosignalsnotebooks as bsnb

# Scientific packages
import numpy
import math
from numpy.random import normal
from scipy.signal import butter, filtfilt, lfilter

In [2]:
# Base packages used in OpenSignals Tools Notebooks for plotting data
from bokeh.plotting import figure, output_file, show, curdoc
from bokeh.io import output_notebook
from bokeh.layouts import column, row
from bokeh.models import ColumnDataSource, Plot, LinearAxis, BoxAnnotation, Arrow, VeeHead, LinearAxis, Range1d
output_notebook(hide_banner=True)

<p class="steps">2 - Use of filtfilt in a generated sine function</p>

In [3]:
# Let's create a sine signal to understand how the filtfilt works
sine_time = numpy.arange(0, 2, .01)
sine_signal = numpy.sin(2*math.pi*sine_time*.5)

# Let's add some random noise to our new signal
noisy_signal = sine_signal + numpy.random.randn(len(sine_time))*0.1

# Creating a Butterworth filter with order 3 and critical frequency of 0.05
[b, a] = butter(3, 0.05)
lfilter_signal = lfilter(b, a, noisy_signal) # apply the filter normally
filfilt_signal = filtfilt(b, a, noisy_signal) # apply the filtfilt filtering

In [4]:
# Let's plot our example
p = figure(plot_width=400, plot_height=250)
p.ygrid.grid_line_alpha=0.5
p.line(sine_time, sine_signal, line_width=2, line_color='black', legend_label='Original signal')
p.line(sine_time, noisy_signal, line_width=2, line_color='blue', legend_label='Noisy signal', line_alpha=0.5)

q = figure(plot_width=400, plot_height=250)
q.ygrid.grid_line_alpha=0.5
q.line(sine_time, noisy_signal, line_width=2, line_color='blue', legend_label='Noisy signal', line_alpha=0.5)
q.line(sine_time, lfilter_signal, line_width=2, line_dash='dashed', line_color='green', legend_label='Normal filter')

r = figure(plot_width=400, plot_height=250)
r.ygrid.grid_line_alpha=0.5
r.line(sine_time, noisy_signal, line_width=2, line_color='blue', legend_label='Noisy signal', line_alpha=0.5)
r.line(sine_time, filfilt_signal, line_width=2, line_dash='dashed', line_color='red', legend_label='Filtfilt')

show(row(p,q,r))

We can see how the application of the one dimensional filter causes a clear misalignement in the signal's phase. The filtfilt filtering solves this issue, and zeros the phase response to match the original prefiltered signal.

<p class="steps">3 - Application to real life signals</p>

In [5]:
def print_filtfilt_plots(time, signal, lfilter_signal, filtfilt_signal):
    p = figure(plot_width=400, plot_height=200)
    p.ygrid.grid_line_alpha=0.5
    p.line(time, signal, line_width=1, legend_label='Original signal')

    q = figure(plot_width=400, plot_height=200)
    q.ygrid.grid_line_alpha=0.5
    q.line(time, signal, line_width=2, line_color='blue', legend_label='Original signal', line_alpha=0.5)
    q.line(time, lfilter_signal, line_width=2, line_dash='dashed', line_color='green', legend_label='Filter')

    r = figure(plot_width=400, plot_height=200)
    r.ygrid.grid_line_alpha=0.5
    r.line(time, signal, line_width=2, line_color='blue', legend_label='Original signal', line_alpha=0.5)
    r.line(time, filtfilt_signal, line_width=2, line_dash='dashed', line_color='red', legend_label='Filfilt')
    
    return p,q,r

<p class="steps">3.1 - ECG signal example</p>

In [6]:
# Load of data
data, header = bsnb.load("../../signal_samples/ecg_20_sec_100_Hz.h5", get_header=True)
channel = list(data.keys())[0]

# Sampling frequency and acquired data
fs = header["sampling rate"]
ch = "CH1" # Channel
resolution = header['resolution'] # Resolution (number of available bits)

# Signal Samples
signal_raw = data[channel]
time = numpy.linspace(0, len(signal_raw) / fs, len(signal_raw))

# Let's convert the signal's units, since we know it is a ECG signal
vcc = 3000 # mV
gain = 1000
signal = (((numpy.array(signal_raw) / 2**resolution) - 0.5) * vcc) / gain

In [7]:
# Creating a Butterworth filter with order 3 and critical frequency of 0.5
[b, a] = butter(3, 0.5)
lfilter_signal = lfilter(b, a, signal)
filtfilt_signal = filtfilt(b, a, signal)

In [8]:
# Let's plot our example
p,q,r = print_filtfilt_plots(time, signal, lfilter_signal, filtfilt_signal)

p.x_range = Range1d(0, 1)
q.x_range = Range1d(0, 1)
r.x_range = Range1d(0, 1)

show(row(p,q,r))

<p class="steps">3.2 - EEG signal example</p>


In [10]:
# Load of data
data, header = bsnb.load("../../signal_samples/signal_sample_single_hub_EEG_2018_7_4.h5", get_header=True)
channel = list(data.keys())[0]

# Sampling frequency and acquired data
ch = "CH1" # Channel
fs = header["sampling rate"]
resolution = header['resolution'] # Resolution (number of available bits)

# Signal Samples
signal_raw = data[channel]
time = numpy.linspace(0, len(signal_raw) / fs, len(signal_raw))

# Let's convert the signal's units, since we know it is a EEG signal
vcc = 3e6 # uV
gain = 40000
signal = (((numpy.array(signal_raw) / 2**resolution) - 0.5) * vcc) / gain

In [11]:
# Creating a Butterworth filter with order 3 and critical frequency of 0.05
[b, a] = butter(3, 0.05)
lfilter_signal = lfilter(b, a, signal)
filtfilt_signal = filtfilt(b, a, signal)

In [12]:
# Let's plot our example
p,q,r = print_filtfilt_plots(time, signal, lfilter_signal, filtfilt_signal)

p.x_range = Range1d(7, 8)
q.x_range = Range1d(7, 8)
r.x_range = Range1d(7, 8)

show(row(p,q,r))

<p class="steps">3.3 - EMG signal example</p>


In [14]:
# Load of data
data, header = bsnb.load("../../signal_samples/emg_bursts.h5", get_header=True)
channel = list(data.keys())[0]

# Sampling frequency and acquired data
ch = "CH1" # Channel
fs = header["sampling rate"]
resolution = header['resolution'] # Resolution (number of available bits)

# Signal Samples
signal_raw = data[channel]
time = numpy.linspace(0, len(signal_raw) / fs, len(signal_raw))

# Let's convert the signal's units, since we know it is a EMG signal
vcc = 3000
gain = 1000
signal = (((numpy.array(signal_raw) / 2**resolution) - 0.5) * vcc) / gain

In [15]:
# Creating a Butterworth filter with order 3 and critical frequency of 0.25
[b, a] = butter(3, 0.25)
lfilter_signal = lfilter(b, a, signal)
filtfilt_signal = filtfilt(b, a, signal)

In [16]:
# Let's plot our example
p,q,r = print_filtfilt_plots(time, signal, lfilter_signal, filtfilt_signal)

p.x_range = Range1d(1.9, 2.1)
q.x_range = Range1d(1.9, 2.1)
r.x_range = Range1d(1.9, 2.1)

p.y_range = Range1d(-1, 0.39)
q.y_range = Range1d(-1, 0.39)
r.y_range = Range1d(-1, 0.39)

p.legend.location = "bottom_right"
q.legend.location = "bottom_right"
r.legend.location = "bottom_right"

show(row(p,q,r))

As a conclusion, we have seen that conventional filtering reduces noise in the signal, but has the side effect of delaying the filtered signal's phase. This poses a problem when we require a high temporal precision for event detection in a time series. Filtfilt handles this problem by applying the same filter forwards and backwards, reducing the time offset to zero. 

It is important to mention that filtfilt cannot be used with differentiator and Hilbert FIR filters, or more generally any filter that depends heavily on the signal's phase.

<strong><span class="color4">We hope that you have enjoyed this tutorial. You can keep learning by checking the many other available <a href="../MainFiles/biosignalsnotebooks.ipynb">Notebooks <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a></span></strong> ! 

<span class="color6">**Auxiliary Code Segment (should not be replicated by the user)**</span>

In [17]:
bsnb.css_style_apply()

.................... CSS Style Applied to Jupyter Notebook .........................
